<a href="https://colab.research.google.com/github/Worachet-Ch/project2022/blob/main/random_nan_and_imputation_with_weight_variable_pynb.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [40]:
import pandas as pd #นำเข้า pandas แทนที่ด้วย pd
import os# os ใช้จัดการกับไฟล์ ว่าอยู่ที่ไหน
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import missingno as mno
import missingno as msno
from sklearn import linear_model
%matplotlib inline
import matplotlib
import sklearn 
from sklearn.impute import KNNImputer
from sklearn.metrics import mean_squared_error
import time

In [41]:
from google.colab import drive #เชื่อม Google drive
drive.mount('/content/drive')
path = '/content/drive/My Drive/project' #เข้า drive
data_file_path = os.path.join(path,'data_notmissing.csv') #ไปที่ไฟล์ confirmed-cases-since-280265.csv
data = pd.read_csv(data_file_path) #อ่านไฟล์ csv

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [42]:
data

Unnamed: 0  Sex  AgeSYear  telomere length (kb)   Weight  Height   BMI  \
0            56    2      57.0                   6.36    47.4   153.0  20.2   
1            85    2      24.0                   9.71    53.2   157.0  21.6   
2           103    2      62.0                   6.17    54.4   165.0  20.0   
3           111    2      35.0                   7.23    56.3   161.0  21.7   
4           156    1      46.0                   6.52    72.3   170.0  25.0   
..          ...  ...       ...                    ...     ...     ...   ...   
148         728    1      60.0                   5.81    72.0   170.0  24.9   
149         729    1      58.0                   5.05    62.0   168.0  22.0   
150         731    2      42.0                   9.48    55.5   165.0  20.4   
151         734    2      61.0                   6.06    61.8   159.0  24.4   
152         739    2      31.0                   9.44    58.2   169.0  20.4   

     Systolic  Diastolic  HeartRate  ...  003_Creatinine  004_Uric Acid  \
0       114.0       75.0       69.0  ...             1.0            5.0   
1       103.0       69.0       78.0  ...             0.8            5.2   
2        95.0       75.0       83.0  ...             0.7            4.1   
3        95.0       57.0       72.0  ...             0.6            5.0   
4       133.0       77.0      107.0  ...             0.9            6.9   
..        ...        ...        ...  ...             ...            ...   
148     131.0       74.0       69.0  ...             0.9            6.9   
149     103.0       76.0       72.0  ...             1.0            6.8   
150     102.0       52.0       77.0  ...             0.8            4.7   
151     117.0       60.0       72.0  ...             0.8            5.1   
152     108.0       69.0       73.0  ...             0.7            4.3   

     005_Cholesterol  006_Triglyceride  008_HDL-C  009_LDL  010_AST  012_ALT  \
0              176.0              51.0       72.0     94.0     16.0     16.0   
1              159.0              45.0       52.0     98.0     13.0     17.0   
2              230.0              94.0       61.0    151.0     18.0     31.0   
3              198.0              47.0       68.0    120.0     16.0     20.0   
4              194.0              63.0       60.0    122.0     15.0     19.0   
..               ...               ...        ...      ...      ...      ...   
148            182.0             179.0       39.0    107.0     36.0     31.0   
149            191.0              62.0       47.0    132.0     16.0     33.0   
150            212.0              68.0       63.0    135.0     11.0     16.0   
151            235.0              66.0       56.0    166.0     15.0     23.0   
152            200.0              44.0       56.0    135.0     14.0     21.0   

     013_Alkaline Phos  071_HbA1c  
0                 62.0        5.1  
1                 50.0        5.4  
2                 76.0        5.6  
3                 35.0        5.1  
4                 69.0        5.2  
..                 ...        ...  
148               79.0        6.5  
149               42.0        6.8  
150               33.0        4.8  
151               44.0        5.4  
152               31.0        4.7  

[153 rows x 28 columns]

### Normalized ด้วยวิธี MinMaxScaler

In [43]:
from sklearn.preprocessing import MinMaxScaler
scaler = MinMaxScaler()
Scaler = scaler.fit_transform(data)
data1 = pd.DataFrame(Scaler)

In [44]:
data1=data1.rename(columns={0: 'Sex' ,1: 'AgeSYear', 2:'telomere length (kb)',3:'Weight',4:'Height',5:'BMI',6:'Systolic',7:'Diastolic',8:'HeartRate',9:'SMM',10:'Fat Mass',
                                       11:'% Body fat',12:'waist to hip radio',13:'abdominal circumference',14:'visceral fat area',15:'Glucose',16:'BUN',17:'Creatinine',18:'Uric Acid',19:'Cholesterol',
                                       20:'Triglyceride',21:'HDL-C',22:'LDL',23:'AST',24:'ALT',25:'Alkaline Phos',26:'HbA1c'}).round(4)
data1

Sex  AgeSYear  telomere length (kb)  Weight  Height     BMI  Systolic  \
0    0.0000       1.0                0.6607  0.2759  0.1274  0.1818    0.2845   
1    0.0425       1.0                0.0714  0.7202  0.2394  0.2727    0.4052   
2    0.0688       1.0                0.7500  0.2507  0.2625  0.4545    0.2672   
3    0.0805       1.0                0.2679  0.3912  0.2992  0.3636    0.4138   
4    0.1464       0.0                0.4643  0.2971  0.6081  0.5682    0.6983   
..      ...       ...                   ...     ...     ...     ...       ...   
148  0.9839       0.0                0.7143  0.2029  0.6023  0.5682    0.6897   
149  0.9854       0.0                0.6786  0.1021  0.4093  0.5227    0.4397   
150  0.9883       1.0                0.3929  0.6897  0.2838  0.4545    0.3017   
151  0.9927       1.0                0.7321  0.2361  0.4054  0.3182    0.6466   
152  1.0000       1.0                0.1964  0.6844  0.3359  0.5455    0.3017   

     Diastolic  HeartRate     SMM  ...  Uric Acid  Cholesterol  Triglyceride  \
0       0.4444     0.6216  0.3103  ...        0.6       0.5172        0.4091   
1       0.2698     0.4595  0.4655  ...        0.4       0.5517        0.2803   
2       0.1429     0.6216  0.5517  ...        0.3       0.3621        0.8182   
3       0.1429     0.1351  0.3621  ...        0.2       0.5172        0.5758   
4       0.7460     0.6757  0.9655  ...        0.5       0.8448        0.5455   
..         ...        ...     ...  ...        ...          ...           ...   
148     0.7143     0.5946  0.3103  ...        0.5       0.8448        0.4545   
149     0.2698     0.6486  0.3621  ...        0.6       0.8276        0.5227   
150     0.2540     0.0000  0.4483  ...        0.4       0.4655        0.6818   
151     0.4921     0.2162  0.3621  ...        0.4       0.5345        0.8561   
152     0.3492     0.4595  0.3793  ...        0.3       0.3966        0.5909   

      HDL-C     LDL     AST     ALT  Alkaline Phos   HbA1c      27  
0    0.1323  0.7407  0.2909  0.1186         0.0000  0.5823  0.4262  
1    0.1089  0.3704  0.3273  0.0678         0.0323  0.4304  0.4754  
2    0.2996  0.5370  0.8091  0.1525         0.4839  0.7595  0.5082  
3    0.1167  0.6667  0.5273  0.1186         0.1290  0.2405  0.4262  
4    0.1790  0.5185  0.5455  0.1017         0.0968  0.6709  0.4426  
..      ...     ...     ...     ...            ...     ...     ...  
148  0.6304  0.1296  0.4091  0.4576         0.4839  0.7975  0.6557  
149  0.1751  0.2778  0.6364  0.1186         0.5484  0.3291  0.7049  
150  0.1984  0.5741  0.6636  0.0339         0.0000  0.2152  0.3770  
151  0.1907  0.4444  0.9455  0.1017         0.2258  0.3544  0.4754  
152  0.1051  0.4444  0.6636  0.0847         0.1613  0.1899  0.3607  

[153 rows x 28 columns]

# 10 % random nan

In [45]:
t_start = time.time()
for i in range(1,1001):
  globals()[f'weight{i}'] = data1.copy() # for loop variable name
  np.random.seed(i) # for loop seed
  n = int((153*10/100)) 
  index_nan = np.random.choice(globals()[f'weight{i}']['Weight'].size, n, replace=False) #globals()[name dataframe][column name].size
  globals()[f'weight{i}']['Weight'].ravel()[index_nan] = np.nan
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

เวลาที่ใช้ในการประมวลผล 0.16461443901062012 วินาที
เวลาที่ใช้ในการประมวลผล 0.0027435739835103353 นาที


In [46]:
weight1

Sex  AgeSYear  telomere length (kb)  Weight  Height     BMI  Systolic  \
0    0.0000       1.0                0.6607  0.2759  0.1274  0.1818    0.2845   
1    0.0425       1.0                0.0714  0.7202  0.2394  0.2727    0.4052   
2    0.0688       1.0                0.7500  0.2507  0.2625  0.4545    0.2672   
3    0.0805       1.0                0.2679  0.3912  0.2992  0.3636    0.4138   
4    0.1464       0.0                0.4643  0.2971  0.6081  0.5682    0.6983   
..      ...       ...                   ...     ...     ...     ...       ...   
148  0.9839       0.0                0.7143  0.2029  0.6023  0.5682    0.6897   
149  0.9854       0.0                0.6786  0.1021  0.4093  0.5227    0.4397   
150  0.9883       1.0                0.3929  0.6897  0.2838  0.4545    0.3017   
151  0.9927       1.0                0.7321  0.2361  0.4054  0.3182    0.6466   
152  1.0000       1.0                0.1964  0.6844  0.3359  0.5455    0.3017   

     Diastolic  HeartRate     SMM  ...  Uric Acid  Cholesterol  Triglyceride  \
0       0.4444     0.6216  0.3103  ...        0.6       0.5172        0.4091   
1       0.2698     0.4595  0.4655  ...        0.4       0.5517        0.2803   
2       0.1429     0.6216  0.5517  ...        0.3       0.3621        0.8182   
3       0.1429     0.1351  0.3621  ...        0.2       0.5172        0.5758   
4       0.7460     0.6757  0.9655  ...        0.5       0.8448        0.5455   
..         ...        ...     ...  ...        ...          ...           ...   
148     0.7143     0.5946  0.3103  ...        0.5       0.8448        0.4545   
149     0.2698     0.6486  0.3621  ...        0.6       0.8276        0.5227   
150     0.2540     0.0000  0.4483  ...        0.4       0.4655        0.6818   
151     0.4921     0.2162  0.3621  ...        0.4       0.5345        0.8561   
152     0.3492     0.4595  0.3793  ...        0.3       0.3966        0.5909   

      HDL-C     LDL     AST     ALT  Alkaline Phos   HbA1c      27  
0    0.1323  0.7407  0.2909  0.1186         0.0000  0.5823  0.4262  
1    0.1089  0.3704  0.3273  0.0678         0.0323  0.4304  0.4754  
2    0.2996  0.5370  0.8091  0.1525         0.4839  0.7595  0.5082  
3    0.1167  0.6667  0.5273  0.1186         0.1290  0.2405  0.4262  
4    0.1790  0.5185  0.5455  0.1017         0.0968  0.6709  0.4426  
..      ...     ...     ...     ...            ...     ...     ...  
148  0.6304  0.1296  0.4091  0.4576         0.4839  0.7975  0.6557  
149  0.1751  0.2778  0.6364  0.1186         0.5484  0.3291  0.7049  
150  0.1984  0.5741  0.6636  0.0339         0.0000  0.2152  0.3770  
151  0.1907  0.4444  0.9455  0.1017         0.2258  0.3544  0.4754  
152  0.1051  0.4444  0.6636  0.0847         0.1613  0.1899  0.3607  

[153 rows x 28 columns]

## Imputation using Mean

In [47]:
from sklearn.impute import SimpleImputer

In [48]:
t_start = time.time()
mean10_imputer = SimpleImputer(strategy='mean')
for i in range(1,1001):
  globals()[f'imputed_mean10_{i}'] = mean10_imputer.fit_transform(globals()[f'weight{i}'].copy()) #for loop miss forest impputation 
  globals()[f'MSE_MEAN10_{i}'] = mean_squared_error(data, globals()[f'imputed_mean10_{i}']) # for loop mean_squared_error
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklea

เวลาที่ใช้ในการประมวลผล 5.435975074768066 วินาที
เวลาที่ใช้ในการประมวลผล 0.09059958457946778 นาที


/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklea

In [49]:
t_start = time.time()
mse_mean10_total = 0 
MSE_MEAN10_1001 = 0
for i in range(0,1001):
  mse_mean10_total = mse_mean10_total + globals()[f'MSE_MEAN10_{i+1}']
AMSE_weight10_mean = mse_mean10_total/1000
print(f'AMSE_weight10_mean = {AMSE_weight10_mean}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_weight10_mean = 13523.49697186706
เวลาที่ใช้ในการประมวลผล 0.0024271011352539062 วินาที
เวลาที่ใช้ในการประมวลผล 4.04516855875651e-05 นาที


## Imputation using the miss forest

In [50]:
import sys
import sklearn.neighbors._base
sys.modules['sklearn.neighbors.base'] = sklearn.neighbors._base
!pip install missingpy
import missingpy
from missingpy import MissForest
from sklearn.metrics import mean_squared_error

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [51]:
t_start = time.time()
MF10_imputer = MissForest()
for i in range(1,1001):
  globals()[f'imputed_mf10_{i}'] = MF10_imputer.fit_transform(globals()[f'weight{i}'].copy()) #for loop miss forest impputation 
  globals()[f'MSE_MF10_{i}'] = mean_squared_error(data, globals()[f'imputed_mf10_{i}']) # for loop mean_squared_error
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(


Iteration: 0


/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(


Iteration: 1


/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(


...

Iteration: 2


/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(


Iteration: 3


/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(


Iteration: 4
เวลาที่ใช้ในการประมวลผล 954.6186621189117 วินาที
เวลาที่ใช้ในการประมวลผล 15.910311035315196 นาที


In [52]:
t_start = time.time()
mse_mf10_total = 0 
MSE_MF10_1001 = 0
for i in range(0,1001):
  mse_mf10_total = mse_mf10_total + globals()[f'MSE_MF10_{i+1}']
AMSE_weight10_mf = mse_mf10_total/1000
print(f'AMSE_weight10_mf = {AMSE_weight10_mf}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_weight10_mf = 13523.495459900761
เวลาที่ใช้ในการประมวลผล 0.007587909698486328 วินาที
เวลาที่ใช้ในการประมวลผล 0.0001264651616414388 นาที


## Imputation using the KNN

In [53]:
from sklearn import neighbors
from sklearn.impute import KNNImputer

In [54]:
t_start = time.time()
KNN10_imputer = KNNImputer(n_neighbors = 15)
for i in range(1,1001):
  globals()[f'imputed_KNN10_{i}'] = KNN10_imputer.fit_transform(globals()[f'weight{i}'].copy())
  globals()[f'MSE_KNN10_{i}'] = mean_squared_error(data, globals()[f'imputed_KNN10_{i}'])
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklea

เวลาที่ใช้ในการประมวลผล 6.794423341751099 วินาที
เวลาที่ใช้ในการประมวลผล 0.11324038902918497 นาที


/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklea

In [55]:
t_start = time.time()
mse_knn10_total = 0 
MSE_KNN10_1001 = 0
for i in range(0,1001):
  mse_knn10_total = mse_knn10_total + globals()[f'MSE_KNN10_{i+1}']
AMSE_weight10_knn = mse_knn10_total/1000
print(f'AMSE_weight10_knn = {AMSE_weight10_knn}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_weight10_knn = 13523.495325956603
เวลาที่ใช้ในการประมวลผล 0.002476215362548828 วินาที
เวลาที่ใช้ในการประมวลผล 4.127025604248047e-05 นาที


## Imputation using the MICE

In [56]:
from sklearn.experimental import enable_iterative_imputer
from sklearn.impute import IterativeImputer
from sklearn.linear_model import LinearRegression
from sklearn import svm

### LinearRegression model

In [57]:
t_start = time.time()
lr = LinearRegression()
for i in range(1,1001):
  imp = IterativeImputer(estimator= lr , max_iter= 10, verbose=2, imputation_order='roman',initial_strategy = 'mean',random_state= i)
  globals()[f'imputed_lr10_{i}'] = imp.fit_transform(globals()[f'weight{i}'].copy())
  globals()[f'MSE_lr10_{i}'] = mean_squared_error(data, globals()[f'imputed_lr10_{i}'])
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(


[IterativeImputer] Completing matrix with shape (153, 28)
[IterativeImputer] Ending imputation round 1/10, elapsed time 0.03
[IterativeImputer] Change: 0.3402887328970105, scaled tolerance: 0.001 
[IterativeImputer] Ending imputation round 2/10, elapsed time 0.05
[IterativeImputer] Change: 0.0, scaled tolerance: 0.001 
[IterativeImputer] Early stopping criterion reached.
[IterativeImputer] Completing matrix with shape (153, 28)
[IterativeImputer] Ending imputation round 1/10, elapsed time 0.02
[IterativeImputer] Change: 0.3828009932618382, scaled tolerance: 0.001 
[IterativeImputer] Ending imputation round 2/10, elapsed time 0.05
[IterativeImputer] Change: 0.0, scaled tolerance: 0.001 
[IterativeImputer] Early stopping criterion reached.
[IterativeImputer] Completing matrix with shape (153, 28)
[IterativeImputer] Ending imputation round 1/10, elapsed time 0.02
[IterativeImputer] Change: 0.5026219995371008, scaled tolerance: 0.001 


/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(


[IterativeImputer] Ending imputation round 2/10, elapsed time 0.06
[IterativeImputer] Change: 0.0, scaled tolerance: 0.001 
[IterativeImputer] Early stopping criterion reached.
[IterativeImputer] Completing matrix with shape (153, 28)
[IterativeImputer] Ending imputation round 1/10, elapsed time 0.02
[IterativeImputer] Change: 0.21381538703709807, scaled tolerance: 0.001 
[IterativeImputer] Ending imputation round 2/10, elapsed time 0.05
[IterativeImputer] Change: 0.0, scaled tolerance: 0.001 
[IterativeImputer] Early stopping criterion reached.
[IterativeImputer] Completing matrix with shape (153, 28)
[IterativeImputer] Ending imputation round 1/10, elapsed time 0.02
[IterativeImputer] Change: 0.40073425140857455, scaled tolerance: 0.001 
[IterativeImputer] Ending imputation round 2/10, elapsed time 0.04
[IterativeImputer] Change: 0.0, scaled tolerance: 0.001 
[IterativeImputer] Early stopping criterion reached.
[IterativeImputer] Completing matrix with shape (153, 28)
[IterativeImput

/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(


...

[IterativeImputer] Ending imputation round 2/10, elapsed time 0.06
[IterativeImputer] Change: 0.0, scaled tolerance: 0.001 
[IterativeImputer] Early stopping criterion reached.
[IterativeImputer] Completing matrix with shape (153, 28)
[IterativeImputer] Ending imputation round 1/10, elapsed time 0.02
[IterativeImputer] Change: 0.32756145340432036, scaled tolerance: 0.001 
[IterativeImputer] Ending imputation round 2/10, elapsed time 0.05
[IterativeImputer] Change: 0.0, scaled tolerance: 0.001 
[IterativeImputer] Early stopping criterion reached.
[IterativeImputer] Completing matrix with shape (153, 28)
[IterativeImputer] Ending imputation round 1/10, elapsed time 0.02
[IterativeImputer] Change: 0.2849235447940282, scaled tolerance: 0.001 
[IterativeImputer] Ending imputation round 2/10, elapsed time 0.05
[IterativeImputer] Change: 0.0, scaled tolerance: 0.001 
[IterativeImputer] Early stopping criterion reached.
[IterativeImputer] Completing matrix with shape (153, 28)
[IterativeImpute

/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklea

[IterativeImputer] Ending imputation round 2/10, elapsed time 0.05
[IterativeImputer] Change: 0.0, scaled tolerance: 0.001 
[IterativeImputer] Early stopping criterion reached.
[IterativeImputer] Completing matrix with shape (153, 28)
[IterativeImputer] Ending imputation round 1/10, elapsed time 0.03
[IterativeImputer] Change: 0.396314116913908, scaled tolerance: 0.001 
[IterativeImputer] Ending imputation round 2/10, elapsed time 0.05
[IterativeImputer] Change: 0.0, scaled tolerance: 0.001 
[IterativeImputer] Early stopping criterion reached.
[IterativeImputer] Completing matrix with shape (153, 28)
[IterativeImputer] Ending imputation round 1/10, elapsed time 0.03
[IterativeImputer] Change: 0.2779474208029898, scaled tolerance: 0.001 
[IterativeImputer] Ending imputation round 2/10, elapsed time 0.05
[IterativeImputer] Change: 0.0, scaled tolerance: 0.001 
[IterativeImputer] Early stopping criterion reached.
[IterativeImputer] Completing matrix with shape (153, 28)
[IterativeImputer]

/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(


[IterativeImputer] Ending imputation round 1/10, elapsed time 0.03
[IterativeImputer] Change: 0.38001583746739154, scaled tolerance: 0.001 
[IterativeImputer] Ending imputation round 2/10, elapsed time 0.06
[IterativeImputer] Change: 0.0, scaled tolerance: 0.001 
[IterativeImputer] Early stopping criterion reached.
เวลาที่ใช้ในการประมวลผล 61.567599296569824 วินาที
เวลาที่ใช้ในการประมวลผล 1.0261266549428305 นาที


In [58]:
t_start = time.time()
mse_lr10_total = 0 
MSE_lr10_1001 = 0
for i in range(0,1001):
  mse_lr10_total = mse_lr10_total + globals()[f'MSE_lr10_{i+1}']
AMSE_weight10_lr = mse_lr10_total/1000
print(f'AMSE_weight10_lr = {AMSE_weight10_lr}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_weight10_lr = 13523.495336041859
เวลาที่ใช้ในการประมวลผล 0.0013382434844970703 วินาที
เวลาที่ใช้ในการประมวลผล 2.230405807495117e-05 นาที


### Support Vector Machine model

In [59]:
t_start = time.time()
regr = svm.SVR()
for i in range(1,1001):
  svm_svr = IterativeImputer(estimator= regr, max_iter= 10, verbose=2, imputation_order='roman',initial_strategy = 'mean',random_state= i)
  globals()[f'imputed_svm10_{i}'] = svm_svr.fit_transform(globals()[f'weight{i}'].copy())
  globals()[f'MSE_svm10_{i}'] = mean_squared_error(data, globals()[f'imputed_svm10_{i}'])
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

[IterativeImputer] Completing matrix with shape (153, 28)
[IterativeImputer] Ending imputation round 1/10, elapsed time 0.04
[IterativeImputer] Change: 0.27254179052475724, scaled tolerance: 0.001 
[IterativeImputer] Ending imputation round 2/10, elapsed time 0.08
[IterativeImputer] Change: 0.0, scaled tolerance: 0.001 
[IterativeImputer] Early stopping criterion reached.
[IterativeImputer] Completing matrix with shape (153, 28)
[IterativeImputer] Ending imputation round 1/10, elapsed time 0.04
[IterativeImputer] Change: 0.3424311783686959, scaled tolerance: 0.001 
[IterativeImputer] Ending imputation round 2/10, elapsed time 0.09
[IterativeImputer] Change: 0.0, scaled tolerance: 0.001 
[IterativeImputer] Early stopping criterion reached.


/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(


[IterativeImputer] Completing matrix with shape (153, 28)
[IterativeImputer] Ending imputation round 1/10, elapsed time 0.05
[IterativeImputer] Change: 0.31538460202998025, scaled tolerance: 0.001 
[IterativeImputer] Ending imputation round 2/10, elapsed time 0.09
[IterativeImputer] Change: 0.0, scaled tolerance: 0.001 
[IterativeImputer] Early stopping criterion reached.
[IterativeImputer] Completing matrix with shape (153, 28)
[IterativeImputer] Ending imputation round 1/10, elapsed time 0.04
[IterativeImputer] Change: 0.2208303087994225, scaled tolerance: 0.001 
[IterativeImputer] Ending imputation round 2/10, elapsed time 0.09
[IterativeImputer] Change: 0.0, scaled tolerance: 0.001 
[IterativeImputer] Early stopping criterion reached.
[IterativeImputer] Completing matrix with shape (153, 28)
[IterativeImputer] Ending imputation round 1/10, elapsed time 0.04
[IterativeImputer] Change: 0.3689804260431918, scaled tolerance: 0.001 


/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(


[IterativeImputer] Ending imputation round 2/10, elapsed time 0.09
[IterativeImputer] Change: 0.0, scaled tolerance: 0.001 
[IterativeImputer] Early stopping criterion reached.
[IterativeImputer] Completing matrix with shape (153, 28)
[IterativeImputer] Ending imputation round 1/10, elapsed time 0.05
[IterativeImputer] Change: 0.26914272105784165, scaled tolerance: 0.001 
[IterativeImputer] Ending imputation round 2/10, elapsed time 0.09
[IterativeImputer] Change: 0.0, scaled tolerance: 0.001 
[IterativeImputer] Early stopping criterion reached.
[IterativeImputer] Completing matrix with shape (153, 28)
[IterativeImputer] Ending imputation round 1/10, elapsed time 0.04
[IterativeImputer] Change: 0.22784683058306676, scaled tolerance: 0.001 
[IterativeImputer] Ending imputation round 2/10, elapsed time 0.09
[IterativeImputer] Change: 0.0, scaled tolerance: 0.001 
[IterativeImputer] Early stopping criterion reached.
[IterativeImputer] Completing matrix with shape (153, 28)


...

[IterativeImputer] Ending imputation round 2/10, elapsed time 0.10
[IterativeImputer] Change: 0.0, scaled tolerance: 0.001 
[IterativeImputer] Early stopping criterion reached.
[IterativeImputer] Completing matrix with shape (153, 28)
[IterativeImputer] Ending imputation round 1/10, elapsed time 0.05
[IterativeImputer] Change: 0.29755820353196344, scaled tolerance: 0.001 
[IterativeImputer] Ending imputation round 2/10, elapsed time 0.09
[IterativeImputer] Change: 0.0, scaled tolerance: 0.001 
[IterativeImputer] Early stopping criterion reached.
[IterativeImputer] Completing matrix with shape (153, 28)
[IterativeImputer] Ending imputation round 1/10, elapsed time 0.05
[IterativeImputer] Change: 0.2791577775061837, scaled tolerance: 0.001 
[IterativeImputer] Ending imputation round 2/10, elapsed time 0.09
[IterativeImputer] Change: 0.0, scaled tolerance: 0.001 
[IterativeImputer] Early stopping criterion reached.

/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(



[IterativeImputer] Completing matrix with shape (153, 28)
[IterativeImputer] Ending imputation round 1/10, elapsed time 0.04
[IterativeImputer] Change: 0.2918828487443414, scaled tolerance: 0.001 
[IterativeImputer] Ending imputation round 2/10, elapsed time 0.09
[IterativeImputer] Change: 0.0, scaled tolerance: 0.001 
[IterativeImputer] Early stopping criterion reached.
[IterativeImputer] Completing matrix with shape (153, 28)
[IterativeImputer] Ending imputation round 1/10, elapsed time 0.05
[IterativeImputer] Change: 0.22236064936059868, scaled tolerance: 0.001 
[IterativeImputer] Ending imputation round 2/10, elapsed time 0.09
[IterativeImputer] Change: 0.0, scaled tolerance: 0.001 
[IterativeImputer] Early stopping criterion reached.
[IterativeImputer] Completing matrix with shape (153, 28)


/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(


[IterativeImputer] Ending imputation round 1/10, elapsed time 0.06
[IterativeImputer] Change: 0.2638087301708802, scaled tolerance: 0.001 
[IterativeImputer] Ending imputation round 2/10, elapsed time 0.10
[IterativeImputer] Change: 0.0, scaled tolerance: 0.001 
[IterativeImputer] Early stopping criterion reached.
[IterativeImputer] Completing matrix with shape (153, 28)
[IterativeImputer] Ending imputation round 1/10, elapsed time 0.04
[IterativeImputer] Change: 0.2837293596316543, scaled tolerance: 0.001 
[IterativeImputer] Ending imputation round 2/10, elapsed time 0.08
[IterativeImputer] Change: 0.0, scaled tolerance: 0.001 
[IterativeImputer] Early stopping criterion reached.
[IterativeImputer] Completing matrix with shape (153, 28)
[IterativeImputer] Ending imputation round 1/10, elapsed time 0.05
[IterativeImputer] Change: 0.2908072799117286, scaled tolerance: 0.001 
[IterativeImputer] Ending imputation round 2/10, elapsed time 0.10
[IterativeImputer] Change: 0.0, scaled toleran

In [60]:
t_start = time.time()
mse_svm10_total = 0 
MSE_svm10_1001 = 0
for i in range(0,1001):
  mse_svm10_total = mse_svm10_total + globals()[f'MSE_svm10_{i+1}']
AMSE_weight10_svm = mse_svm10_total/1000
print(f'AMSE_weight10_svm = {AMSE_weight10_svm}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_weight10_svm = 13523.494977003513
เวลาที่ใช้ในการประมวลผล 0.0038154125213623047 วินาที
เวลาที่ใช้ในการประมวลผล 6.359020868937174e-05 นาที


### New Section

In [61]:
from sklearn.ensemble import RandomForestRegressor

## Imputation using the EM

### impy.em

In [62]:
!pip install impyute
import impyute as impy

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [63]:
t_start = time.time()
for i in range(1,1001):
  globals()[f'imputed_impy10_{i}'] = impy.em(globals()[f'weight{i}'].values.copy())
  globals()[f'MSE_impy10_{i}'] = mean_squared_error(data, globals()[f'imputed_impy10_{i}'])
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

เวลาที่ใช้ในการประมวลผล 8.829944610595703 วินาที
เวลาที่ใช้ในการประมวลผล 0.1471657435099284 นาที


In [64]:
t_start = time.time()
mse_impy10_total = 0 
MSE_impy10_1001 = 0
for i in range(0,1001):
  mse_impy10_total = mse_impy10_total + globals()[f'MSE_impy10_{i+1}']
AMSE_weight10_impy = mse_impy10_total/1000
print(f'AMSE_weight10_impy = {AMSE_weight10_impy}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_weight10_impy = 13523.501244471208
เวลาที่ใช้ในการประมวลผล 0.013135194778442383 วินาที
เวลาที่ใช้ในการประมวลผล 0.00021891991297403972 นาที


### GMM

In [65]:
from sklearn.mixture import GaussianMixture

In [66]:
GaussianMixture(n_components=1,max_iter=100, random_state=1).fit(weight1['Weight'].copy())

ValueError: ignored